# General imports

In [ ]:
import numpy as np
import scipy.optimize
import sympy
from scipy.interpolate import RegularGridInterpolator
from tqdm.notebook import tqdm
from sympy.utilities.lambdify import lambdify
from pathlib import Path

# Plotting imports

In [ ]:
import matplotlib
import matplotlib.pyplot as plt

matplotlib.use("agg")

%matplotlib inline
%config InlineBackend.figure_format = 'svg'


params = {
    "backend": "ps",
    "axes.labelsize": 22,
    "font.size": 13,
    "legend.fontsize": 10,
    "xtick.labelsize": 22,
    "ytick.labelsize": 22,
    "text.usetex": True,
    "font.family": "serif",
    "font.serif": "Computer Modern Roman",
    "legend.frameon": True,
    "savefig.dpi": 300,
}

plt.rcParams.update(params)
plt.rc("text.latex", preamble=r"\usepackage{xfrac}\usepackage{siunitx}")

# Create data folders

In [ ]:
Path('data').mkdir(exist_ok=True)
Path('publication/figures').mkdir(parents=True, exist_ok=True)

# Classical circuit

In [ ]:
EJ0 = 1
EJ1 = 0.5
EJ2 = 0.25
ϕs = np.linspace(-np.pi, np.pi, 101)


def circuit_energy(ϕ0, ϕ1, ϕ2):
    return -EJ0 * np.cos(ϕ0) - EJ1 * np.cos(ϕ0 - ϕ1) - EJ2 * np.cos(ϕ0 - ϕ2)


def ϕ0_min(ϕ1, ϕ2):
    return scipy.optimize.brute(
        lambda ϕ0: circuit_energy(ϕ0, ϕ1, ϕ2), [(-np.pi, np.pi)]
    )[0]


try:
    ϕ0s = np.load("data/phi0.npy")
    Is_cut = np.load("data/classical_Is.npy")
except FileNotFoundError:
    ϕ0s = np.array([ϕ0_min(ϕ1, ϕ2) for ϕ2 in ϕs for ϕ1 in ϕs])
    ϕ0s = ϕ0s.reshape(len(ϕs), len(ϕs))
    # Compute current through lines in parameter space
    Is_cut = np.array(
        [[np.sin(ϕ0_min(ϕ1, -ϕ1 + offset)) for ϕ1 in ϕs] for offset in tqdm(ϕs)]
    )
    np.save("data/phi0", ϕ0s)
    np.save("data/classical_Is", Is_cut)

ϕ1s, ϕ2s = np.meshgrid(ϕs, ϕs)

In [ ]:
fig, ax = plt.subplots()

x = ϕs
y = -ϕs + ϕs[34]
x = np.arctan2(np.sin(x), np.cos(x))
y = np.arctan2(np.sin(y), np.cos(y))
# Add nan at discontinuity
pos = np.where(np.abs(np.diff(y)) >= 0.5)[0] + 1
x = np.insert(x, pos, np.nan)
y = np.insert(y, pos, np.nan)
ax.plot(x, y, c="black", ls="--")

im = ax.imshow(
    np.sin(ϕ0s),
    cmap="coolwarm",
    origin="lower",
    interpolation="bilinear",
    extent=(min(ϕs), max(ϕs), min(ϕs), max(ϕs)),
)
plt.colorbar(im)

# Axis labels and title
ax.set_xlabel("$\phi_1$")
ax.set_ylabel("$\phi_2$")
ax.set_title("$I^0 \Phi_0 / E_{J,0}$", fontsize=18)

# Labels in ticks
vals = [-np.pi, 0, np.pi]
labels = [r"$-\pi$", r"$0$", r"$\pi$"]
ax.set_xticks(vals)
ax.set_xticklabels(labels)
ax.set_yticks(vals)
ax.set_yticklabels(labels)

left, bottom, width, height = [0.27, 0.23, 0.3, 0.3]
ax2 = fig.add_axes([left, bottom, width, height])
ax2.set_xlim(-np.pi, np.pi)
ax2.plot(ϕs, Is_cut[30])
ax2.axhline(np.average(Is_cut[34]), ls="--")
ax2.set_xticks(vals)
ax2.set_xticklabels(labels, fontsize=15)
ax2.set_yticks([-0.5, 0, 0.5])
ax2.set_yticklabels([-0.5, 0, 0.5], fontsize=15)
ax2.set_xlabel("$\phi_1$", fontsize=15)

plt.savefig("publication/figures/classical_current.pdf", bbox_inches="tight")

In [ ]:
fig, ax = plt.subplots()
ax.set_xlim(-np.pi, np.pi)
ax.plot(ϕs, [np.trapz(Is_cut[i], ϕs) / (2 * np.pi) for i in range(len(ϕs))])
ax.set_xticks(vals)
ax.set_xticklabels(labels)
ax.set_xlabel("$\phi_1 + \phi_2$")
ax.set_title(
    "$\langle I^0( \phi_1(0) + Vt, \phi_2(0) - Vt) \\rangle \Phi_0 / E_{J,0}$",
    fontsize=18,
)
plt.savefig("publication/figures/current_phase.pdf", bbox_inches="tight")

## Quantum mechanical circuit

In [ ]:
NUM_STATES = 21
ECs = np.logspace(-3, 2, 50)


def hamiltonian(ϕ1, ϕ2, EC, ng):
    assert NUM_STATES % 2 == 1
    ham = np.zeros((NUM_STATES, NUM_STATES), dtype="complex128")

    # Josephson coupling
    for EJ, ϕ in zip([EJ0, EJ1, EJ2], [0, ϕ1, ϕ2]):
        off_diag = np.diag(np.ones(NUM_STATES - 1), k=-1)
        ham += -EJ / 2 * np.exp(-1j * ϕ) * off_diag
    ham += ham.T.conj()

    # Charge terms
    n_max = (NUM_STATES - 1) // 2
    ham += EC * np.diag((np.arange(-n_max, n_max + 1) - ng) ** 2)

    return ham


def grad_hamiltonian(ϕ1, ϕ2, EC, ng, axis):
    EJ = [EJ1, EJ2][axis]
    ϕ = [ϕ1, ϕ2][axis]
    off_diag = np.diag(np.ones(NUM_STATES - 1), k=-1)
    ham = 1j * EJ / 2 * np.exp(-1j * ϕ) * off_diag
    ham += ham.T.conj()
    return ham


def berry_curvature(ϕ1, ϕ2, EC, ng):
    h = hamiltonian(ϕ1, ϕ2, EC, ng)
    eigvals, eigvecs = np.linalg.eigh(h)
    dh = np.array([grad_hamiltonian(ϕ1, ϕ2, EC, ng, ax) for ax in range(2)])
    de = eigvals[0] - eigvals
    gs = eigvecs[:, 0]

    # Create tensor <gs|dH/dϕ_m|n>
    aux = np.einsum("i,mij,jn->mn", gs.conj(), dh, eigvecs)

    # Set this to infinity so we cancel term n = gs
    de[0] = np.inf
    term1 = np.einsum("mi,ni,i->mn", aux, aux.conj(), 1 / de ** 2)
    term2 = np.einsum("ni,mi,i->mn", aux, aux.conj(), 1 / de ** 2)

    curvature = 1j * (term1 - term2)
    assert np.allclose(curvature.imag, 0)

    return curvature.real

### Compute adiabatic contribution

In [ ]:
def gs_energy(ϕ1, ϕ2, EC, ng):
    return np.linalg.eigvalsh(hamiltonian(ϕ1, ϕ2, EC, ng))[0]


try:
    es = np.load("data/gs_energy.npy")
    es_degen = np.load("data/degen_gs_energy.npy")
except FileNotFoundError:
    es = np.array([np.vectorize(gs_energy)(ϕ1s, ϕ2s, EC, 0.4).T for EC in tqdm(ECs)])
    es_degen = np.array(
        [np.vectorize(gs_energy)(ϕ1s, ϕ2s, EC, 0.5).T for EC in tqdm(ECs)]
    )
    np.save("data/gs_energy", es)
    np.save("data/degen_gs_energy", es_degen)

In [ ]:
def ground_current(es):
    return np.gradient(es, ϕs, axis=0).T + np.gradient(es, ϕs, axis=1).T


I0 = ground_current(np.vectorize(gs_energy)(ϕ1s, ϕ2s, 30, 0).T)

fig, ax = plt.subplots()
im = ax.imshow(
    I0,
    cmap="coolwarm",
    origin="lower",
    interpolation="bilinear",
    vmax=0.025, vmin=-0.025,
    extent=(min(ϕs), max(ϕs), min(ϕs), max(ϕs)),
)
cbar = plt.colorbar(im)
cbar.set_ticks([-0.025, 0, 0.025])
cbar.set_ticklabels(["-0.025", "0.0", "0.025"])

# Axis labels and title
ax.set_xlabel("$\phi_1$")
ax.set_ylabel("$\phi_2$")
ax.set_title("$I^0 \Phi_0 / E_{J,0}$", fontsize=18)

# Labels in ticks
vals = [-np.pi, 0, np.pi]
labels = [r"$-\pi$", r"$0$", r"$\pi$"]
ax.set_xticks(vals)
ax.set_xticklabels(labels)
ax.set_yticks(vals)
ax.set_yticklabels(labels)

plt.savefig("publication/figures/quantum_current.pdf", bbox_inches="tight")

### Analytical expression for quartet supercurrent in the high charging energy limit

In [ ]:
_E1, _EJ0, _EJ1, _EJ2, _ϕ1, _ϕ2 = sympy.symbols(
    "E_1, E_{J0}, E_{J1}, E_{J2}, \phi_1, \phi_2", real=True
)

matrix_element = (
    _EJ1 * sympy.exp(sympy.I * _ϕ1) + _EJ2 * sympy.exp(sympy.I * _ϕ2) + _EJ0
).rewrite(sympy.cos) / 2

H = sympy.Matrix([[0, matrix_element], [matrix_element.conjugate(), _E1]])
gs_en = list(H.eigenvals().keys())[0]
I = sympy.simplify(sympy.diff(gs_en, _ϕ1) + sympy.diff(gs_en, _ϕ2))
I

In [ ]:
subs = [(_EJ0, 1), (_EJ1, 0.5), (_EJ2, 0.25)]
analytical_curr = lambdify([_E1, _ϕ1, _ϕ2], I.subs(subs))


def analytical_max_curr(EC, ng):
    currs = np.array(
        [[analytical_curr(EC*(1-2*ng), ϕ1, -ϕ1 + offset)for ϕ1 in ϕs] for offset in ϕs]
    )
    return np.max([np.trapz(currs[i], ϕs) / (2 * np.pi) for i in range(len(ϕs))])


def max_current(currs):
    def quadrant(angle):
        return np.arctan2(np.sin(angle), np.cos(angle))

    ifun = RegularGridInterpolator((ϕs, ϕs), currs)
    offsets = np.linspace(-np.pi, np.pi, 101)
    pts = [[[ϕ, quadrant(-ϕ + o)] for ϕ in ϕs] for o in offsets]
    return np.max([np.trapz(ifun(p), ϕs) / (2 * np.pi) for p in pts])

In [ ]:
plt.figure()
plt.semilogx(ECs, [max_current(ground_current(e)) for e in es],
             label="$n_g=0.4$ (full)")
plt.plot(ECs[27:], [analytical_max_curr(EC, 0.4) for EC in ECs[27:]],
         c='C0', ls='--', label="$n_g=0.4$ (analytical)")
plt.semilogx(ECs, [max_current(ground_current(e)) for e in es_degen],
             label="$n_g=0.5$ (full)")
xmin = (np.log10(ECs[27]) - np.log10(ECs[0])) / (np.log10(ECs[-1]) - np.log10(ECs[0]))
plt.axhline(analytical_max_curr(0, 0.5),
            xmin=xmin,
            c='C1', ls='--', label="$n_g=0.5$ (analytical)")
plt.xlabel("$E_C / E_{J,0}$")
plt.title("$I^0_\mathrm{max}\Phi_0 / E_{J,0}$", fontsize=18)
plt.xlim(min(ECs), max(ECs))
plt.yticks([0, 0.05, 0.1])
plt.legend(fontsize=14)
plt.savefig("publication/figures/I_max.pdf", bbox_inches="tight")

### Berry curvature contribution

In [ ]:
ng = 0.7
offset = -1


def berry_aux(ϕ1, ϕ2, EC, ng):
    return berry_curvature(ϕ1, ϕ2, EC, ng)[0, 1]


try:
    Ωs = np.load("data/berry.npy")
    Ωs_cut = np.load("data/berry_cut.npy")
except FileNotFoundError:
    Ωs = np.vectorize(berry_aux)(ϕ1s, ϕ2s, 1, ng)
    Ωs_cut = [berry_aux(ϕ1, -ϕ1 + offset, 1, ng) for ϕ1 in ϕs]
    np.save("data/berry", Ωs)
    np.save("data/berry_cut", Ωs_cut)

In [ ]:
fig, ax = plt.subplots()

x = ϕs
y = -ϕs + offset
x = np.arctan2(np.sin(x), np.cos(x))
y = np.arctan2(np.sin(y), np.cos(y))
# Add nan at discontinuity
pos = np.where(np.abs(np.diff(y)) >= 0.5)[0] + 1
x = np.insert(x, pos, np.nan)
y = np.insert(y, pos, np.nan)
ax.plot(x, y, c="black", ls="--")

im = ax.imshow(
    Ωs,
    cmap="PuOr_r",
    origin="lower",
    interpolation="bilinear",
    extent=(np.min(ϕ1s), np.max(ϕ1s), np.min(ϕ2s), np.max(ϕ2s)),
)
plt.colorbar(im)

# Axis labels and title
ax.set_xlabel("$\phi_1$")
ax.set_ylabel("$\phi_2$")
ax.set_title("$\Omega_{12}$", fontsize=18)

# Labels in ticks
vals = [-np.pi, 0, np.pi]
labels = [r"$-\pi$", r"$0$", r"$\pi$"]
ax.set_xticks(vals)
ax.set_xticklabels(labels)
ax.set_yticks(vals)
ax.set_yticklabels(labels)

plt.savefig("publication/figures/berry_curvature.pdf", bbox_inches="tight")

In [ ]:
fig, ax = plt.subplots()

ax.plot(ϕs, Ωs_cut)
ax.set_xlim(-np.pi, np.pi)
ax.set_xticks(vals)
ax.set_xticklabels(labels)
ax.set_yticks([0, 0.1])
ax.set_xlabel("$\phi_1$")
ax.set_title("$\Omega_{12}$", fontsize=18)

plt.savefig("publication/figures/berry_curvature_cut.pdf", bbox_inches="tight")